# Interpolation Using images in video

In this notebook we will attempt to analyze an image and recreate it by using newton interpolation

# Funciones Basicas

In [1]:
import math as m
import numpy as np
from sympy import *

def f(f):
    x = Symbol("x")
    e = m.e
    pi = m.pi
    f = eval(f)
    return f
def g(g):
    x = Symbol("x")
    e = m.e
    pi = m.pi
    g = eval(g)
    return g
def f1(f):
    x = Symbol("x")
    e = m.e
    pi = m.pi
    f1 = diff(f)
    return f1
def f2(f1):
    x = Symbol("x")
    e = m.e
    pi = m.pi
    f2 = diff(f1)
    return f2
def evalfunct(f,y):
    x = Symbol("x")
    e = m.e
    pi = m.pi
    evalf = f.subs(x,y)
    return evalf
def regresiva(a,b):
    n = len(b)
    x = [0 for i in range(n)]
    x[n-1] = b[n-1,0]/a[n-1,n-1]
    for i in reversed(range(0,n-1)):
        suma = 0
        for j in range((i+1),n):
            suma = suma + a[i,j]*x[j]
        x[i] = (b[i,0] - suma)/a[i,i]
    return x
def progresiva(a,b):
    n = len(b)
    x = [0 for i in range(n)]
    x[0] = b[0,0]/a[0,0]
    for i in range(1,n):
        suma = 0
        for j in range(0,(i-1)):
            suma = suma + a[i,j]*x[j]
        x[i] = (b[i,0] - suma)/a[i,i]
    return x
def intercambioFila(a,fi1,fi2):
    f = np.copy(a)
    f[fi1,:] = a[fi2,:]
    f[fi2,:] = a[fi1,:]
    return f
def intercambioColumna(a,c1,c2):
    f = np.copy(a)
    f[:,[c1]] = a[:,[c2]]
    f[:,[c2]] = a[:,[c1]]
    return f

def pivoteoParcial(a,b,k):
    s = np.hstack(((a,b)))
    n = len(s) - 1
    mayor = abs(k)
    filaMayor = k
    for t in range(k,n):
        if abs(s[t,k]) > mayor:
            mayor = abs(s[t,k])
            filaMayor = t
    if mayor == 0:
        print("The system doesnt have a unique solution")
    elif filaMayor != k :
        s = intercambioFila(s,filaMayor,k)
    s = s[:,:-1]
    return s
def pivoteoTotal(a,b,k):
    s = np.hstack(((a,b)))
    n = len(a) - 1
    marcas = np.matrix('1 2 3 4')
    mayor = 0
    filaMayor = k
    columnaMayor = k
    for r in range (k,n):
        for t in range (k,n):
            if(abs(s[r,t]) > mayor):
                mayor = abs(s[r,t])
                filaMayor = r
                columnaMayor = t
    if mayor == 0:
        print("The system doesnt have a unique solution")
    elif filaMayor != k:
        s = intercambioFila(s,filaMayor,k)
    elif columnaMayor != k:
        s = intercambioColumna(s,columnaMayor,k)
        marcas = intercambioColumna(marcas,columnaMayor,k)
    s = s[:,:-1]
    print("The system is: ", marcas)
    return s
import numpy as np
#import matplotlib.pyplot as plt

def coef(x, y):
    x#.astype(float)
    y#.astype(float)
    n = len(x)
    a = []
    for i in range(n):
        a.append(y[i])

    for j in range(1, n):

        for i in range(n-1, j-1, -1):
            a[i] = (a[i]-a[i-1])/(x[i]-x[i-j])

    return np.array(a) # return an array of coefficient

def Eval(a, x, r):
    x#.astype(float)
    n = len( a ) - 1
    temp = a[n] + (r - x[n])
    for i in range( n - 1, -1, -1 ):
        temp = temp * ( r - x[i] ) + a[i]
    return temp # return the y_value interpolation

## Format Data

In order to process the data, we will format the pixels of each image as a numeric array

In [2]:
from PIL import Image
import pandas as pd
import numpy  as np
from scipy.interpolate import CubicSpline
import matplotlib.pyplot as plt

def get_colors(image):
    img = Image.open(image,'r')
    pix_val_r = list(img.getdata(0))
    pix_val_g = list(img.getdata(1))
    pix_val_b = list(img.getdata(2))
    df = pd.DataFrame(pix_val_r, columns =['r'])
    df.insert(1, value = pix_val_g, column = 'g')
    df.insert(2, value = pix_val_b, column = 'b')
    return df

### Getting images

We are currently using the dataset provided by The 2017 DAVIS Challenge (1). In this case, we will take two images from a video in order to interpolate them and compare the behaviour of the provided pixels. First, we get the images and formt them using the following functions. The result is a dataframe with RGB parameters for each pixel

In [3]:
img1 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00000.jpg'
img2 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00001.jpg'
img3 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00002.jpg'
img4 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00003.jpg'

df_img1 = get_colors(img1)
df_img2 = get_colors(img2)
df_img3 = get_colors(img3)
df_img4 = get_colors(img4)

## Data interpolation

using the dataset we selected three images from a video and got the numeric values for the colors of each pixel. In this case we will implemente multiple interpolation methods between image1 and image3

# DiffNewton

In [61]:
import numpy as np
#from funciones import *
import sys
#strx = str(raw_input("Please enter the vector of x: "))
#strfx = str(raw_input("Please enter the vector of Fx: "))
#strval = str(raw_input("Please enter the value to interpolate"))
def NewtonDiff(strx, strfx):
#strx = '2 2.2 2.4 2.6 2.8'
    x = np.fromstring(strx, dtype=float, sep=' ')
#strfx = '-4.6109 -4.1749 -3.3768 -2.1362 -0.3553'
    fx = np.fromstring(strfx, dtype=float, sep=' ')
    strval = '2.5'
    val = float(strval)
    n = len(x)
    a = []
    for i in range(n):
        a.append(fx[i])
    for j in range(1, n):
        for i in range(n-1, j-1, -1):
            a[i] = (a[i]-a[i-1])/(x[i]-x[i-j])
    a = np.array(a)
    n = len( a ) - 1
    temp = a[n] + (val - x[n])
    for i in range( n - 1, -1, -1 ):
        temp = temp * ( val - x[i] ) + a[i]
    result = temp
    return result

In [74]:
img1 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00000.jpg'
img2 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00001.jpg'
img3 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00002.jpg'
img4 = 'DAVIS-2017-trainval-480p\\DAVIS\\JPEGImages\\480p\\bear\\00003.jpg'

df_img1 = get_colors(img1)
df_img2 = get_colors(img2)
df_img3 = get_colors(img3)
df_img4 = get_colors(img4)

In [75]:
def color_to_str(color):
    listToStr = ' '.join(map(str, color)) 
    return listToStr

In [76]:
red1 = color_to_str(df_img1['r'])
red2 = color_to_str(df_img2['r'])
red3 = color_to_str(df_img3['r'])
red4 = color_to_str(df_img4['r'])

In [77]:
listred1 = df_img1['r']
listred2 = df_img2['r']
listred3 = df_img3['r']
listred4 = df_img4['r']
test2 = '1 2 3 4'
i = 0
size = df_img1.shape[0]
while(i < size):
    test = str(listred1[i]) + ' ' + str(listred2[i])+ ' ' + str(listred3[i])+ ' ' + str(listred4[i])
    print(NewtonDiff(test2,test))
    # aqui crear un df con la comuna R y llenarlo con lo de arriba
    i+= 1
#print(iterpolation)

43.8125
41.6875
39.1875
46.8125
49.0
51.9375
64.75
66.375
68.125
73.1875
72.4375
71.6875
71.3125
70.125
71.1875
70.75
70.0
64.5625
66.375
68.5625
65.0
69.4375
73.375
68.3125
71.75
73.9375
75.6875
77.1875
78.25
80.5
79.8125
77.9375
80.9375
75.625
65.625
65.75
63.5625
54.1875
56.5625
63.5625
64.25
64.25
63.1875
65.5
67.75
65.5625
65.6875
65.8125
65.75
62.5
60.625
63.0
65.0
66.375
67.0
68.3125
66.875
65.1875
63.25
59.5625
51.625
48.0625
44.4375
40.25
45.5625
47.9375
53.6875
59.75
64.5625
66.0625
67.75
69.3125
67.0625
70.625
69.0625
63.875
61.4375
59.875
57.125
56.125
61.875
66.3125
68.5
72.1875
76.1875
75.375
73.6875
76.125
75.75
73.1875
74.0625
75.8125
75.625
76.5
78.9375
76.6875
78.0625
78.5625
78.9375
78.1875
76.6875
73.8125
69.6875
70.1875
64.625
65.875
70.1875
72.375
75.0
77.5
75.1875
74.5625
70.6875
69.4375
68.1875
68.1875
68.8125
71.5625
73.8125
75.625
79.25
78.8125
78.4375
79.5
80.5625
82.6875
84.4375
84.625
85.75
83.75
81.125
75.125
68.375
65.0625
61.0
56.375
61.0
60.75
63.0
69.6

83.1875
85.75
95.375
92.6875
93.375
95.9375
96.5625
95.5
95.0625
94.625
88.8125
92.6875
89.1875
84.9375
81.0625
77.9375
78.25
77.3125
78.9375
86.5625
93.5625
93.125
89.0
83.0625
81.0625
82.8125
83.25
85.75
88.9375
90.875
91.75
93.125
92.3125
89.4375
90.8125
89.0
91.0625
94.0625
94.9375
96.5625
96.75
96.6875
96.1875
95.625
93.875
93.375
95.25
90.4375
82.1875
84.5625
84.3125
73.625
70.9375
66.3125
63.9375
64.5
69.9375
72.3125
80.6875
90.5625
91.3125
90.0
89.5625
87.875
88.4375
88.375
86.5
89.6875
92.0
92.6875
93.875
96.8125
97.875
96.5625
94.8125
91.9375
88.125
87.8125
89.625
91.6875
90.9375
89.5625
88.6875
88.8125
91.0
92.875
92.4375
92.6875
93.875
94.5625
97.125
95.5625
87.125
78.375
71.8125
58.3125
52.0
56.4375
53.625
60.0
66.625
67.8125
69.0
69.875
65.375
63.375
53.875
51.1875
49.5
46.375
41.8125
40.75
41.8125
42.75
50.5625
54.625
55.8125
62.5625
73.9375
77.375
79.4375
87.625
91.125
86.625
84.1875
81.9375
81.125
85.8125
88.5625
82.375
76.75
80.1875
80.1875
82.3125
86.1875
90.6875
95.

93.625
98.375
97.9375
90.125
93.5
104.125
105.125
103.8125
100.6875
102.1875
106.625
105.0
105.0625
109.9375
106.9375
103.6875
109.4375
100.6875
91.625
100.625
103.3125
96.25
98.9375
110.9375
108.0
108.1875
113.1875
118.125
116.125
117.125
113.25
122.0625
131.6875
124.25
106.625
93.9375
90.5625
84.125
76.8125
87.5625
89.0
94.9375
107.125
112.4375
106.0625
111.375
102.375
71.9375
70.25
82.5
71.75
71.5
88.25
93.375
94.8125
79.125
89.75
103.8125
107.5
115.25
103.1875
91.6875
113.875
105.75
84.375
82.5
77.25
63.125
52.0625
63.25
61.8125
57.5
58.375
61.625
65.0
72.75
84.8125
89.25
78.8125
86.0625
82.0
79.8125
87.8125
88.4375
81.0
82.0625
90.0
79.8125
82.125
81.625
81.125
87.875
79.0625
75.3125
57.6875
53.0625
53.25
51.375
50.6875
55.75
72.9375
81.75
84.9375
90.4375
88.4375
89.4375
104.75
102.5625
99.25
104.5
90.625
76.4375
74.875
66.25
55.625
62.8125
65.4375
63.0
67.0625
69.25
67.3125
70.5
97.3125
129.4375
112.5
119.0625
169.625
171.1875
169.3125
191.1875
184.625
135.125
120.6875
115.9375
7

99.8125
96.0
112.875
119.75
117.125
103.6875
95.625
101.75
100.8125
97.25
95.3125
84.125
73.625
73.125
75.8125
72.25
68.1875
62.8125
74.375
79.5625
86.75
84.9375
87.6875
89.8125
90.6875
95.6875
99.9375
95.9375
87.875
88.625
86.6875
87.125
89.1875
89.9375
91.9375
93.9375
92.875
89.25
87.5
84.6875
79.9375
75.875
80.5
71.125
62.25
69.6875
65.1875
67.1875
77.3125
84.5
86.5625
91.375
104.25
103.5625
107.125
103.5625
102.125
104.75
106.1875
99.25
96.4375
102.1875
91.9375
89.4375
86.625
78.75
82.6875
82.75
70.875
69.1875
63.875
52.4375
37.4375
58.5
91.0625
89.1875
126.5
158.375
168.375
149.0
108.4375
110.375
115.4375
71.625
52.1875
45.375
48.5625
51.375
49.4375
45.9375
47.75
41.5
42.9375
23.875
26.4375
25.1875
43.3125
63.875
63.75
61.375
66.5625
82.375
75.8125
76.625
104.625
75.1875
73.1875
58.25
57.9375
53.3125
54.6875
47.75
43.1875
50.75
49.6875
48.8125
57.4375
62.125
63.375
64.9375
67.125
70.0625
71.375
69.9375
63.3125
64.125
63.0
54.5
55.4375
61.625
60.5
66.75
72.5
78.3125
80.125
79.4375


87.6875
89.625
92.9375
92.5625
91.25
93.75
98.75
97.1875
91.125
94.5625
95.4375
83.875
79.25
82.0625
82.1875
81.75
84.875
93.25
97.1875
94.4375
88.625
85.3125
82.0
73.4375
72.5
73.5
73.8125
79.4375
76.5625
75.8125
76.1875
81.5625
79.0
81.875
84.25
89.1875
87.4375
80.6875
85.125
84.25
80.5
81.0625
81.4375
74.8125
72.625
75.6875
76.5
67.9375
69.0
77.0
80.625
76.6875
76.875
81.375
81.8125
79.0
72.8125
70.8125
68.0
66.375
64.25
67.0625
76.6875
75.875
71.75
76.1875
80.3125
75.25
74.3125
79.125
80.75
78.0625
77.5625
77.875
79.8125
83.125
85.4375
85.0
83.9375
84.1875
87.125
84.75
87.1875
94.6875
91.8125
86.1875
89.9375
77.5625
72.25
72.1875
71.375
68.3125
70.6875
75.0625
73.6875
78.625
82.625
74.4375
74.125
79.125
74.125
72.8125
76.75
81.75
76.5625
73.5625
76.9375
77.5625
70.6875
63.25
59.5625
57.625
54.375
50.75
49.6875
52.625
57.375
62.4375
64.5
68.5
68.9375
71.125
73.75
74.1875
75.875
79.1875
82.6875
84.8125
91.875
88.9375
84.8125
81.3125
82.5
86.875
80.875
85.25
82.6875
84.375
95.0
91.0
8

...

63.5625
61.0625
115.5
177.75
179.3125
160.0625
111.4375
107.5625
124.9375
164.6875
157.375
131.0625
121.75
93.5625
57.875
93.75
92.8125
109.1875
132.5
137.5625
165.125
139.6875
151.625
168.875
107.3125
130.8125
129.3125
115.375
109.6875
117.4375
112.8125
103.0
135.9375
140.8125
152.1875
157.6875
174.375
156.1875
120.375
147.0625
149.4375
139.5
175.5
149.25
140.125
146.125
129.6875
127.0625
128.1875
153.125
133.8125
157.375
133.3125
107.9375
113.6875
110.1875
113.8125
116.25
129.75
143.8125
142.375
148.3125
151.5
155.4375
157.5625
170.6875
178.625
187.3125
172.0
176.5
168.625
157.375
152.125
136.6875
136.3125
150.4375
120.0
122.8125
113.875
95.3125
93.5
98.0
73.0
72.1875
98.125
82.1875
112.6875
110.1875
96.5625
120.125
116.875
101.0
75.75
103.4375
127.3125
142.375
184.1875
189.8125
144.25
153.875
116.1875
105.125
150.0625
180.6875
214.375
216.0625
159.5
174.625
169.0625
164.625
200.9375
199.125
186.0625
187.25
184.625
191.5625
192.6875
176.6875
188.8125
181.625
180.0
158.25
140.375
131.

101.625
87.0
66.8125
58.625
58.875
57.4375
69.875
68.75
64.75
53.75
47.125
51.5
49.75
54.875
64.0625
67.4375
76.0
88.0625
88.5
85.625
86.5625
87.75
85.9375
68.375
54.875
46.4375
34.5625
34.875
47.8125
58.1875
64.375
55.0
53.0625
54.75
49.625
56.875
53.4375
43.1875
46.9375
39.625
37.0
51.125
53.0
50.25
58.5
62.8125
62.0625
54.3125
41.875
39.8125
40.1875
40.8125
46.5625
43.125
40.0
42.5
45.5625
47.8125
53.5
51.625
59.75
60.4375
58.1875
49.1875
48.9375
51.0
42.625
36.75
33.4375
37.125
36.5
30.9375
22.75
19.9375
19.25
18.4375
23.875
27.375
31.0625
34.5625
39.6875
45.0625
46.125
44.5
41.4375
39.0
37.875
38.1875
37.875
35.8125
33.6875
33.1875
27.8125
25.25
27.3125
28.5625
25.625
21.9375
19.9375
17.75
17.25
15.6875
16.1875
23.6875
50.375
68.0625
61.75
63.8125
92.9375
83.9375
69.3125
59.0
57.875
55.875
49.125
39.9375
26.5
21.6875
17.3125
15.875
17.875
18.8125
18.625
17.875
20.25
22.125
20.5625
16.75
17.375
26.375
31.875
23.625
18.0
26.4375
97.625
135.125
213.6875
235.125
230.0
191.8125
171.25


112.75
128.75
92.0
101.5
131.375
106.875
118.1875
142.25
129.0
145.8125
176.4375
191.5625
185.4375
163.0
158.9375
163.0
144.8125
166.75
205.375
172.0625
160.8125
157.9375
113.1875
123.6875
129.3125
114.5625
115.625
125.4375
135.25
126.0
109.3125
87.125
55.25
43.0625
37.625
46.9375
51.1875
49.5
56.0625
74.6875
102.9375
126.1875
150.625
152.4375
156.8125
147.0625
142.125
124.6875
131.5625
144.75
161.1875
158.3125
171.4375
194.5
202.1875
159.5625
150.875
172.375
133.9375
126.625
153.875
123.5625
155.625
166.125
138.6875
153.25
100.5625
87.625
110.6875
98.0625
128.25
159.3125
171.6875
141.9375
136.8125
106.25
91.25
81.4375
88.375
104.8125
98.8125
117.8125
136.0
136.4375
160.5625
145.4375
136.875
184.625
136.375
150.0
152.6875
146.625
148.1875
165.1875
165.75
187.0625
159.3125
139.8125
104.875
93.25
111.0
147.625
181.4375
190.125
170.8125
203.125
179.1875
199.125
232.0625
215.3125
188.375
182.0
189.875
182.25
148.625
130.9375
127.375
145.0625
170.25
197.625
161.4375
162.3125
181.6875
175.87

151.9375
166.4375
162.875
160.8125
161.1875
143.375
129.4375
122.8125
125.5
162.0
148.75
160.125
155.0
117.9375
112.1875
116.0625
108.9375
104.4375
115.0625
105.875
121.125
122.0
149.625
189.625
176.5625
176.125
185.25
188.0
156.6875
123.1875
107.875
97.1875
131.9375
173.8125
183.125
185.8125
188.125
161.625
132.5
178.0625
180.8125
164.625
188.375
170.5625
162.0625
168.8125
192.625
197.1875
152.125
142.8125
150.8125
129.625
164.25
173.5625
173.0
161.3125
137.0625
150.6875
141.8125
161.3125
180.375
183.9375
189.75
194.1875
211.4375
239.125
200.625
198.75
144.0
92.875
116.25
97.4375
95.25
121.3125
127.0625
103.0
96.5625
97.6875
94.5625
153.3125
155.875
159.0625
185.1875
166.0625
156.0
152.125
124.625
138.0
142.8125
160.4375
166.5625
167.25
153.875
121.75
154.6875
154.3125
190.9375
225.125
202.75
172.1875
134.875
87.5
107.125
125.25
163.0
165.0
197.5625
171.625
148.5625
148.6875
107.0
110.0625
98.3125
120.4375
140.25
136.75
141.875
160.75
160.875
149.375
133.1875
151.9375
176.3125
172.625

162.1875
152.375
146.125
138.8125
126.3125
135.3125
131.9375
131.0
137.75
141.8125
152.875
168.125
184.6875
200.9375
222.25
215.3125
226.75
228.0
230.6875
228.625
228.5
214.9375
213.5
209.3125
207.0
208.625
198.1875
193.5
205.6875
199.5
219.3125
219.0
213.3125
203.5
182.0
181.1875
194.875
194.875
215.9375
213.75
208.375
206.6875
215.25
212.4375
218.9375
218.8125
214.6875
215.9375
186.75
168.75
168.875
138.125
150.75
157.375
176.1875
188.75
216.8125
228.375
238.25
243.5625
238.0625
242.0
228.6875
200.625
180.3125
143.5625
124.1875
139.8125
171.5625
196.125
216.0625
218.9375
216.1875
215.1875
230.8125
228.0625
230.5625
239.0
227.375
227.3125
224.25
219.375
230.0625
231.375
229.4375
235.6875
222.8125
221.875
200.0
183.5625
161.0
162.25
193.5625
202.5625
229.4375
235.0
208.9375
181.5625
157.75
140.5625
144.125
125.9375
140.25
168.4375
180.1875
194.4375
186.3125
195.0
169.1875
163.5625
166.5625
146.3125
153.4375
150.9375
179.375
217.3125
226.3125
200.0
149.25
132.4375
130.1875
177.6875
216.

# Splines Cubicas